# Proyecto: Predicting Fraud in Financial Payment Services

In [3]:
# Esto es necesario para correr el reporte de pandas_profiling
#pip install ipywidgets

In [1]:
# Cargue de las librerias

import pandas as pd
import numpy as np
import seaborn as sns
%matplotlib inline
import matplotlib.pyplot as plt
import matplotlib.lines as mlines
from mpl_toolkits.mplot3d import Axes3D
from pandas_profiling import ProfileReport
from sklearn.model_selection import train_test_split, learning_curve
from sklearn.metrics import average_precision_score
#from xgboost.sklearn import XGBClassifier
#from xgboost import plot_importance, to_graphviz

In [ ]:
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)

In [5]:
# Import de la base de datos
df = pd.read_csv("D:\OneDrive - Universidad del Norte\Documentos\Maestría Estadística\Semestre III\Machine Learning\Proyecto/PS_20174392719_1491204439457_log.csv")

In [6]:
# Renombrando a las variables
df = df.rename(columns={'oldbalanceOrg':'oldBalanceOrig', 'newbalanceOrig':'newBalanceOrig', \
                        'oldbalanceDest':'oldBalanceDest', 'newbalanceDest':'newBalanceDest'})
print(df.head())

   step      type    amount     nameOrig  oldBalanceOrig  newBalanceOrig  \
0     1   PAYMENT   9839.64  C1231006815        170136.0       160296.36   
1     1   PAYMENT   1864.28  C1666544295         21249.0        19384.72   
2     1  TRANSFER    181.00  C1305486145           181.0            0.00   
3     1  CASH_OUT    181.00   C840083671           181.0            0.00   
4     1   PAYMENT  11668.14  C2048537720         41554.0        29885.86   

      nameDest  oldBalanceDest  newBalanceDest  isFraud  isFlaggedFraud  
0  M1979787155             0.0             0.0        0               0  
1  M2044282225             0.0             0.0        0               0  
2   C553264065             0.0             0.0        1               0  
3    C38997010         21182.0             0.0        1               0  
4  M1230701703             0.0             0.0        0               0  


Se crea un reporte para la previsualización y conocimiento de la base de datos

In [7]:

profile = ProfileReport(df, title='Análisis de las transacciones ', html={'style':{'full_width':True}})
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Transacciones fraudulentas
De los cinco tipos de transacciones. El fraude solo ocurre en dos de ellas: Transfer que es cuando se envía dinero a un cliente del banco (estafador) y Cash out que es cuando se envía dinero a un comerciante para que le pague al cliente (estafador).  

In [ ]:
print('\n Los tipos de transacciones fraudulentas son {}'.format(\
list(df.loc[df.isFraud == 1].type.drop_duplicates().values))) # only 'CASH_OUT' 
                                                             # & 'TRANSFER'

dfFraudTransfer = df.loc[(df.isFraud == 1) & (df.type == 'TRANSFER')] #Transferencias
dfFraudCashout = df.loc[(df.isFraud == 1) & (df.type == 'CASH_OUT')] #Pagos

print ('\n El número de transferencias fraudulentas es = {}'.\
       format(len(dfFraudTransfer))) # 4097

print ('\n El número de pagos fraudulentos es = {}'.\
       format(len(dfFraudCashout))) # 4116


 Los tipos de transacciones fraudulentas son ['TRANSFER', 'CASH_OUT']

 El número de transferencias fraudulentas es = 4097

 El número de pagos fraudulentos es = 4116


## Transacciones con alerta de fraude
Dentro de los tipos de transacciones donde se generó una alerta por posible fraude, solo se encuentró el tipo de transacción *transferencia*. Donde, el monto **mínimo** alertado fue de 353874.22 usd y el **máximo** de 92445516.64 usd.

In [ ]:
print('\nTipos de transacciones en donde se activa la alerta de fraude: \
{}'.format(list(df.loc[df.isFlaggedFraud == 1].type.drop_duplicates()))) 
                                                            # only 'TRANSFER'

dfTransfer = df.loc[df.type == 'TRANSFER']
dfFlagged = df.loc[df.isFlaggedFraud == 1]
dfNotFlagged = df.loc[df.isFlaggedFraud == 0]

print('\nCantidad mínima en donde se activa la alerta de fraude = {}'\
                                  .format(dfFlagged.amount.min())) # 353874.22

print('\nCantidad máxima donde se activa la alerta de fraude =\
 {}'.format(dfTransfer.loc[dfTransfer.isFlaggedFraud == 0].amount.max())) # 92445516.64


Tipos de transacciones en donde se activa la alerta de fraude: ['TRANSFER']

Cantidad mínima en donde se activa la alerta de fraude = 353874.22

Cantidad máxima donde se activa la alerta de fraude = 92445516.64


En las transacciones con alerta de fraude se puede identificar que el viejo y nuevo balance es el mismo en las cuentas de origen y destino. Además, en las transacciones con alerta de fraude el viejo balance de la cuenta destino = 0. Sin embargo, hay transferencias en donde el viejo y el nuevo balance de la cuenta destino son iguales 0 y no son marcadas como alerta de fraude. Así que esta condición no determina que una transacción sea marcada como alerta de fraude. En conclusión esta variable será descartada.  

In [ ]:
df.loc[df.isFlaggedFraud == 1]

step      type       amount     nameOrig  oldBalanceOrig  \
2736446   212  TRANSFER   4953893.08   C728984460      4953893.08   
3247297   250  TRANSFER   1343002.08  C1100582606      1343002.08   
3760288   279  TRANSFER    536624.41  C1035541766       536624.41   
5563713   387  TRANSFER   4892193.09   C908544136      4892193.09   
5996407   425  TRANSFER  10000000.00   C689608084     19585040.37   
5996409   425  TRANSFER   9585040.37   C452586515     19585040.37   
6168499   554  TRANSFER   3576297.10   C193696150      3576297.10   
6205439   586  TRANSFER    353874.22  C1684585475       353874.22   
6266413   617  TRANSFER   2542664.27   C786455622      2542664.27   
6281482   646  TRANSFER  10000000.00    C19004745     10399045.08   
6281484   646  TRANSFER    399045.08   C724693370     10399045.08   
6296014   671  TRANSFER   3441041.46   C917414431      3441041.46   
6351225   702  TRANSFER   3171085.59  C1892216157      3171085.59   
6362460   730  TRANSFER  10000000.00  C2140038573     17316255.05   
6362462   730  TRANSFER   7316255.05  C1869569059     17316255.05   
6362584   741  TRANSFER   5674547.89   C992223106      5674547.89   

         newBalanceOrig     nameDest  oldBalanceDest  newBalanceDest  isFraud  \
2736446      4953893.08   C639921569             0.0             0.0        1   
3247297      1343002.08  C1147517658             0.0             0.0        1   
3760288       536624.41  C1100697970             0.0             0.0        1   
5563713      4892193.09   C891140444             0.0             0.0        1   
5996407     19585040.37  C1392803603             0.0             0.0        1   
5996409     19585040.37  C1109166882             0.0             0.0        1   
6168499      3576297.10   C484597480             0.0             0.0        1   
6205439       353874.22  C1770418982             0.0             0.0        1   
6266413      2542664.27   C661958277             0.0             0.0        1   
6281482     10399045.08  C1806199534             0.0             0.0        1   
6281484     10399045.08  C1909486199             0.0             0.0        1   
6296014      3441041.46  C1082139865             0.0             0.0        1   
6351225      3171085.59  C1308068787             0.0             0.0        1   
6362460     17316255.05  C1395467927             0.0             0.0        1   
6362462     17316255.05  C1861208726             0.0             0.0        1   
6362584      5674547.89  C1366804249             0.0             0.0        1   

         isFlaggedFraud  
2736446               1  
3247297               1  
3760288               1  
5563713               1  
5996407               1  
5996409               1  
6168499               1  
6205439               1  
6266413               1  
6281482               1  
6281484               1  
6296014               1  
6351225               1  
6362460               1  
6362462               1  
6362584               1

In [ ]:
print('\nNúmero de cuentas marcadas como no fraude con viejo balance de la cuenta de destino igual a 0 y\
 nuevo balance de la cuenta de destino igual a 0: {}'.\
format(len(dfTransfer.loc[(dfTransfer.isFlaggedFraud == 0) & \
(dfTransfer.oldBalanceDest == 0) & (dfTransfer.newBalanceDest == 0)]))) # 4158


Número de cuentas marcadas como no fraude con viejo balance de la cuenta de destino igual a 0 y nuevo balance de la cuenta de destino igual a 0: 4158


## Cash in

En esta modalidad de fraude, se le transfiere el dinero a una cuenta (comerciante) que le paga a el estafador. En este caso puede suceder que la cuenta que recibe el dinero sea la misma del estafador. Sin embargo, los datos muestran que no hay cuentas comunes.

In [ ]:
print('\nHay comerciantes entre las cuentas de origen para las trasacciones de pago \
en efectivo? {}'.format(\
(df.loc[df.type == 'CASH_IN'].nameOrig.str.contains('M')).any())) # False


Hay comerciantes entre las cuentas de origen para la trasacciones de pago en efectivo? False


## Cash out
De igual manera sucede con Cash out. No hay cuentas comunes entre las transacciones y las cuentas que sacan el dinero.

In [ ]:
print('\nHay comerciantes entre las cuenta de destino para las trasacciones de retiro \
de efefctivo? {}'.format(\
(df.loc[df.type == 'CASH_OUT'].nameDest.str.contains('M')).any())) # False


Hay comerciantes entre las cuenta de destino para las trasacciones de retiro de efefctivo? False


De hecho, no hay comerciantes entre las cuentas que envian dinero. Solo están en las cuentas que reciben.

In [ ]:
print('\nHay comerciantes entre las cuentas de origen? {}'.format(\
      df.nameOrig.str.contains('M').any())) # False
#
print('\nHay otro tipo de transaccion diferente a pagos para \
 los comerciantes? {}'.format(\
(df.loc[df.nameDest.str.contains('M')].type != 'PAYMENT').any())) # False


Hay comerciantes entre las cuentas de origen? False

Hay otro tipo de transaccion diferente a pagos para  los comerciantes? False


En conclusión, para todas las transacciones  teniendo en cuenta el número de cuenta destino y origen, la etiqueta comerciante aparece de una forma impredecible. Así que esta variable se descarta. 
Dentro de las cuentas receptoras de transferencias puede suceder que algunas cuentas sean originarias de retiros en efectivo. Sin embargo, los datos muestran que no existen esas cuentas.

In [ ]:
#  
print('\nDentro de las transacciones fraudulentas hay cuentas destino \
receptoras de dinero para retiro en efectivo? {}'.format(\
(dfFraudTransfer.nameDest.isin(dfFraudCashout.nameOrig)).any())) # False
dfNotFraud = df.loc[df.isFraud == 0]


Dentro de las transacciones fraudulentas hay cuentas destino receptoras de dinero para retiro en efectivo? False


Algunas cuentas de destino para tranferencias fraudulentas originaron retiros de efeftivo que no fueron detectados como fraude y fueron marcados como retiros genuinos. 

In [ ]:
print('\nFraudulent TRANSFERs whose destination accounts are originators of \
genuine CASH_OUTs: \n\n{}'.format(dfFraudTransfer.loc[dfFraudTransfer.nameDest.\
isin(dfNotFraud.loc[dfNotFraud.type == 'CASH_OUT'].nameOrig.drop_duplicates())]))


Fraudulent TRANSFERs whose destination accounts are originators of genuine CASH_OUTs: 

         step      type      amount     nameOrig  oldBalanceOrig  \
1030443    65  TRANSFER  1282971.57  C1175896731      1282971.57   
6039814   486  TRANSFER   214793.32  C2140495649       214793.32   
6362556   738  TRANSFER   814689.88  C2029041842       814689.88   

         newBalanceOrig     nameDest  oldBalanceDest  newBalanceDest  isFraud  \
1030443             0.0  C1714931087             0.0             0.0        1   
6039814             0.0   C423543548             0.0             0.0        1   
6362556             0.0  C1023330867             0.0             0.0        1   

         isFlaggedFraud  
1030443               0  
6039814               0  
6362556               0  


## 3. Limpieza de los datos
Del Analisis Exploratorio de Datos (AED)nos dimos cuenta que el fraude ocurre solo en las transferencias y los retiros. Por lo tanto vamos a trabajar con una base que tenga solo ese tipo de transacciones

In [9]:
# Se crea un sub data_frame con solo las transacciones TRANSFER y CASH_OUT
X = df.loc[(df.type == 'TRANSFER') | (df.type == 'CASH_OUT')]

randomState = 5
np.random.seed(randomState)

#X = X.loc[np.random.choice(X.index, 100000, replace = False)]

# Se pasa la columna fraude a un objeto llamado Y
Y = X['isFraud']
del X['isFraud']

# Se elimina las columnas irrelevantes para el AED
X = X.drop(['nameOrig', 'nameDest', 'isFlaggedFraud'], axis = 1)


# Se transforma el tipo de transacción en codificación binaria
X.loc[X.type == 'TRANSFER', 'type'] = 0
X.loc[X.type == 'CASH_OUT', 'type'] = 1
X.type = X.type.astype(int) # convert dtype('O') to dtype(int)

### 3.1. Imputación de valores faltantes latentes
La base de datos tiene varias transacciones con balances en 0 en las cuentas receptoras, tanto en el momentos antes y después de una transacción con montos distintos a 0. La proporción de tales transacciones, es mucho más grande en las que son fraudulentas (50%) que en las que son genuinas (0.06%)


In [10]:
# Se separa las observaciones fraudulentas de las que no
Xfraud = X.loc[Y == 1]
XnonFraud = X.loc[Y == 0]

print('\nLa proporción de transacciones FRAUDULENTAS con \'oldBalanceDest\' = \
\'newBalanceDest\' = 0 aun cuando el monto transado \'amount\' sea distinto de 0 es: {}'.\
format(len(Xfraud.loc[(Xfraud.oldBalanceDest == 0) & \
(Xfraud.newBalanceDest == 0) & (Xfraud.amount)]) / (1.0 * len(Xfraud))))

print('\nLa proporción de transacciones GENUINAS con \'oldBalanceDest\' = \
\'newBalanceDest\' = 0 aun cuando el monto transado \'amount\' sea distinto de 0 es: {}'.\
format(len(XnonFraud.loc[(XnonFraud.oldBalanceDest == 0) & \
(XnonFraud.newBalanceDest == 0) & (XnonFraud.amount)]) / (1.0 * len(XnonFraud))))


La proporción de transacciones FRAUDULENTAS con 'oldBalanceDest' = 'newBalanceDest' = 0 aun cuando el monto transado 'amount' sea distinto de 0 es: 0.4955558261293072

La proporción de transacciones GENUINAS con 'oldBalanceDest' = 'newBalanceDest' = 0 aun cuando el monto transado 'amount' sea distinto de 0 es: 0.0006176245277308345


Se hace la misma evaluación para las cuentas de origen

In [11]:
# Se separa las observaciones fraudulentas de las que no
Xfraud = X.loc[Y == 1]
XnonFraud = X.loc[Y == 0]

print('\nLa proporción de transacciones FRAUDULENTAS con \'oldBalanceOrig\' = \
\'newBalanceOrig\' = 0 aun cuando el monto transado \'amount\' sea distinto de 0 es: {}'.\
format(len(Xfraud.loc[(Xfraud.oldBalanceOrig == 0) & \
(Xfraud.newBalanceOrig == 0) & (Xfraud.amount)]) / (1.0 * len(Xfraud))))

print('\nLa proporción de transacciones GENUINAS con \'oldBalanceOrig\' = \
\'newBalanceOrig\' = 0 aun cuando el monto transado \'amount\' sea distinto de 0 es: {}'.\
format(len(XnonFraud.loc[(XnonFraud.oldBalanceOrig == 0) & \
(XnonFraud.newBalanceOrig == 0) & (XnonFraud.amount)]) / (1.0 * len(XnonFraud))))


La proporción de transacciones FRAUDULENTAS con 'oldBalanceOrig' = 'newBalanceOrig' = 0 aun cuando el monto transado 'amount' sea distinto de 0 es: 0.0030439547059539756

La proporción de transacciones GENUINAS con 'oldBalanceOrig' = 'newBalanceOrig' = 0 aun cuando el monto transado 'amount' sea distinto de 0 es: 0.4737321319703598


Dado que el balance en 0 de las cuentas receptoras es un fuerte indicador de fraude, se procede a no hacer imputación del balance de la cuenta (en el momento antes de la transacción) con una distribución con una subsecuente ajuste para los montos transados. Si se hace esto, se maquillaría este indicador de fraude y haría que las transsacciones fraudulentas aparecieran como genuinas. Por lo tanto, se reemplazará el valor de 0 con -1, lo que será más util para la contrucción de un algoritmo de Machine Learning que detecte el fraude.

In [12]:
X.loc[(X.oldBalanceDest == 0) & (X.newBalanceDest == 0) & (X.amount != 0), \
      ['oldBalanceDest', 'newBalanceDest']] = - 1

Así como se demostró, los datos también tienen varias transacciones con balances en 0 en las cuentas de origen, antes y después de una transacción con montos distintos de 0. En este caso la proporción de tales transacciones es mucho menor en los casos de fraude (0.3%) comparado a las transacciones genuinas (47%). De manera similar al razonamiento anterior, en vez de imputar un valor numérico, se reemplaza los 0 con un valor nulo.

In [13]:
X.loc[(X.oldBalanceOrig == 0) & (X.newBalanceOrig == 0) & (X.amount != 0), \
      ['oldBalanceOrig', 'newBalanceOrig']] = np.nan

## 4. Ingeniería de variables
En vista de la posibilidad de que las cuentas con balance 0 sirvan para diferenciar entre las transacciones fraudulentas de las que no,  se tomó el proceso de imputación de la sección 3.1 un paso más allá y se creó dos nuevas columnas que registren el error en términos de monto en las cuentas de origen y receptoras para cada transacción. Estas nuevas variables resultaron ser importantes para obtener el mejor desempeño del algoritmo de ML que se usará al final.

In [14]:
X['errorBalanceOrig'] = X.newBalanceOrig + X.amount - X.oldBalanceOrig
X['errorBalanceDest'] = X.oldBalanceDest + X.amount - X.newBalanceDest

## 5. Visualización de datos
La mejor forma de confirmar que los datos contienen suficiente información para que el algoritmo de ML haga predicciones robustas, es intentar visualizar directamente la diferencia entre las transacciones fraudulentas de las genuinas. Bajo este principio, se visualizarán estas diferencias en los gráficos siguientes.

In [17]:
# Largo de la base
limit = len(X)

# Creación de la función plotStrip
def plotStrip(x, y, hue, figsize = (14, 9)):
    
    fig = plt.figure(figsize = figsize)
    colours = plt.cm.tab10(np.linspace(0, 1, 9))
    with sns.axes_style('ticks'):
        ax = sns.stripplot(x, y, \
             hue = hue, jitter = 0.4, marker = '.', \
             size = 4, palette = colours)
        ax.set_xlabel('')
        ax.set_xticklabels(['genuine', 'fraudulent'], size = 16)
        for axis in ['top','bottom','left','right']:
            ax.spines[axis].set_linewidth(2)

        handles, labels = ax.get_legend_handles_labels()
        plt.legend(handles, ['Transfer', 'Cash out'], bbox_to_anchor=(1, 1), \
               loc=2, borderaxespad=0, fontsize = 16);
    return ax

### 5.1 Dispersión de las transacciones en el tiempo

Este gráfico muestra como las transacciones fraudulentas y las genuinas tienen distintas connotaciones cuando su dispersión es vista en el tiempo. Está claro que las transacciones fraudulentas están más homogeneamente distribuidas en el tiempo en comparación a las genuinas. También es destacable que los retiros superan en número a las transferencias dentro de las transacciones genuinas, en contraste a la distribución balanceada que hay en las transacciones con fraude. Nótese además que se usó el parámetro _jitter_ en la función Plotstrip que se diseñó, para poder separar y diferenciar las transacciones que ocurrian al mismo tiempo.

In [18]:
ax = plotStrip(Y[:limit], X.step[:limit], X.type[:limit])
ax.set_ylabel('time [hour]', size = 16)
ax.set_title('Striped vs. homogenous fingerprints of genuine and fraudulent \
transactions over time', size = 20);

C:\Users\luist\AppData\Local\Temp\ipykernel_7328\1949919385.py:1: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  ax = plotStrip(Y[:limit], X.step[:limit], X.type[:limit])


TypeError: stripplot() takes from 0 to 1 positional arguments but 2 positional arguments (and 4 keyword-only arguments) were given

<Figure size 1400x900 with 0 Axes>

### 5.2 Dispersión de las transacciones en los montos
Los 2 gráficos muestran que aunque  la presencia de fraude en una transacción puede ser discernida por el monto de la transacción original, la variable creada de error en el balance es más efectiva en hacer esta distinción.

In [ ]:
limit = len(X)
ax = plotStrip(Y[:limit], X.amount[:limit], X.type[:limit], figsize = (14, 9))
ax.set_ylabel('amount', size = 16)
ax.set_title('Same-signed fingerprints of genuine \
and fraudulent transactions over amount', size = 18);

### 5.3. Dispersión de los errores en el balance en las cuentas receptoras

In [ ]:
limit = len(X)
ax = plotStrip(Y[:limit], - X.errorBalanceDest[:limit], X.type[:limit], \
              figsize = (14, 9))
ax.set_ylabel('- errorBalanceDest', size = 16)
ax.set_title('Opposite polarity fingerprints over the error in \
destination account balances', size = 18);

### 5.4. Separación de las transacciones genuinas y fraudulentas